## (1) Import libraries

In [2]:
from pycaret.datasets import get_data
from pycaret.anomaly import *

In [1]:
# Record version of key libraries
from importlib.metadata import version

print('pycaret==%s' % version('pycaret'))

pycaret==2.3.1


## (2) Get data

In [4]:
# Get a list of all pre-packaged data
# get_data('index')

# Select a pre-packaged data for testing
data = get_data('anomaly')

Col1      Col2      Col3      Col4      Col5      Col6      Col7  \
0  0.263995  0.764929  0.138424  0.935242  0.605867  0.518790  0.912225   
1  0.546092  0.653975  0.065575  0.227772  0.845269  0.837066  0.272379   
2  0.336714  0.538842  0.192801  0.553563  0.074515  0.332993  0.365792   
3  0.092108  0.995017  0.014465  0.176371  0.241530  0.514724  0.562208   
4  0.325261  0.805968  0.957033  0.331665  0.307923  0.355315  0.501899   

       Col8      Col9     Col10  
0  0.608234  0.723782  0.733591  
1  0.331679  0.429297  0.367422  
2  0.861309  0.899017  0.088600  
3  0.158963  0.073715  0.208463  
4  0.558449  0.885169  0.182754

## (3) Setup pipeline

This step also includes data pre-processing steps such as normalisation and missing values imputation.

Logged data and profile are stored under `mlruns` folder.

In [5]:
# Get relevant column names
numeric_cols = [
    'Col1',
    'Col2',
    'Col3',
    'Col4',
    'Col5',
    'Col6',
    'Col7',
    'Col8',
    'Col9',
    'Col10'
]
categorical_cols = []
ignore_cols = []

# Setup core pycaret config
clf_setup = setup(
    data=data, 
    silent=True,
    numeric_features=numeric_cols,
    categorical_features=categorical_cols,
    ignore_features=ignore_cols,
    imputation_type='simple',
    numeric_imputation='median',
    normalize=True,
    normalize_method='minmax',
    n_jobs=-1,
    preprocess=True,
    session_id=6, 
    log_data=True,
    log_profile=True,
    log_experiment=True, 
    experiment_name='anomaly1')

# Retrieve and save processed data
X_data = get_config('X')
X_data.to_csv('./processed_data.csv', index=False)

# data_processing_pipeline = get_config('prep_pipe')


## (4) Create models

In [6]:
# Select a list of models of interest to be tested
# # To see all available models
# models()

# Pick isolation forest model
iforest_model = create_model('iforest', fraction=0.05)

print(iforest_model)

IForest(behaviour='new', bootstrap=False, contamination=0.05,
    max_features=1.0, max_samples='auto', n_estimators=100, n_jobs=-1,
    random_state=6, verbose=0)


## (5) Assign cluster labels to current data

In [7]:
# Assign cluster using model

iforest_results = assign_model(iforest_model)

iforest_results.head()

Col1      Col2      Col3      Col4      Col5      Col6      Col7  \
0  0.263995  0.764929  0.138424  0.935242  0.605867  0.518790  0.912225   
1  0.546092  0.653975  0.065575  0.227772  0.845269  0.837066  0.272379   
2  0.336714  0.538842  0.192801  0.553563  0.074515  0.332993  0.365792   
3  0.092108  0.995017  0.014465  0.176371  0.241530  0.514724  0.562208   
4  0.325261  0.805968  0.957033  0.331665  0.307923  0.355315  0.501899   

       Col8      Col9     Col10  Anomaly  Anomaly_Score  
0  0.608234  0.723782  0.733591        0      -0.017557  
1  0.331679  0.429297  0.367422        0      -0.066793  
2  0.861309  0.899017  0.088600        1       0.004493  
3  0.158963  0.073715  0.208463        1       0.046974  
4  0.558449  0.885169  0.182754        0      -0.036004

## (6) Assign cluster labels to new data

In [8]:
# Assign cluster using model

iforest_results = predict_model(iforest_model, data=data)

iforest_results.head()

Col1      Col2      Col3      Col4      Col5      Col6      Col7  \
0  0.263995  0.764929  0.138424  0.935242  0.605867  0.518790  0.912225   
1  0.546092  0.653975  0.065575  0.227772  0.845269  0.837066  0.272379   
2  0.336714  0.538842  0.192801  0.553563  0.074515  0.332993  0.365792   
3  0.092108  0.995017  0.014465  0.176371  0.241530  0.514724  0.562208   
4  0.325261  0.805968  0.957033  0.331665  0.307923  0.355315  0.501899   

       Col8      Col9     Col10  Anomaly  Anomaly_Score  
0  0.608234  0.723782  0.733591        0      -0.017557  
1  0.331679  0.429297  0.367422        0      -0.066793  
2  0.861309  0.899017  0.088600        1       0.004493  
3  0.158963  0.073715  0.208463        1       0.046974  
4  0.558449  0.885169  0.182754        0      -0.036004

## (7) Analyze model performance

In [9]:
# Make interactive standard diagnostic plots
evaluate_model(iforest_model)

# plot_model(iforest_model, plot='tsne')
# plot_model(iforest_model, plot='umap')

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Anomaly TSnE (3d)', 'tsn…

## (7) Save model

In [10]:
# Save model

save_model(iforest_model, model_name='best_model')
# iforest_model = load_model('iforest_model')

Transformation Pipeline and Model Succesfully Saved


(Pipeline(memory=None,
          steps=[('dtypes',
                  DataTypes_Auto_infer(categorical_features=[],
                                       display_types=False, features_todrop=[],
                                       id_columns=[], ml_usecase='regression',
                                       numerical_features=['Col1', 'Col2',
                                                           'Col3', 'Col4',
                                                           'Col5', 'Col6',
                                                           'Col7', 'Col8',
                                                           'Col9', 'Col10'],
                                       target='UNSUPERVISED_DUMMY_TARGET',
                                       time_features=[])),
                 ('imputer',
                  Simple_Imputer(categorical_strate...
                 ('fix_perfect', 'passthrough'),
                 ('clean_names', Clean_Colum_Names()),
                 ('feature_